In [ ]:
# label transfer with Seurat?

In [2]:
library(Seurat)
library(dplyr)
library(ggplot2)
library(SingleCellExperiment)

In [3]:
# load reference
heart.ref = readRDS('~/septation/markers/Mantri/Mantri_chicken_heart.rds')

In [4]:
# load list of orthologs
om = read.delim('turtle_chicken_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('turtle', 'chicken', 'LCA', 'homology_type', 'orthology_confidence')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 11338     5

turtle chicken LCA           homology_type    orthology_confidence
10 ND2    ND2     Archelosauria ortholog_one2one 1

In [5]:
# list of stages and samples
stages = rep(c('stage14', 'stage17', 'stage21'), each = 3)
samples = paste0('sample', c('4', '7', '8A', '3_Triangle', '5B', '5Y', '1A', '1B', '2'))

In [6]:
# load data
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(sampleid in 1:length(samples)){
    file0 = paste0(stages[sampleid], '_', samples[sampleid], '_data.rds')
    sce = readRDS(file0)

    # subset to mouse 1-1 orthologs
    genelist <- om$chicken[match(rownames(sce), om$turtle)]
    # genelist[1:10]
    
    exp_mat2 = LayerData(sce, assay = 'RNA', layer = 'counts')
    mtd2 = sce@meta.data
    rownames(exp_mat2) = genelist
    exp_mat2 <- exp_mat2[!is.na(rownames(exp_mat2)) & !duplicated(rownames(exp_mat2)),]

    # dim(exp_mat2)
    heart.query = CreateSeuratObject(counts = exp_mat2, meta.data = mtd2)

    # select two technologies for the query datasets
    heart.query <- NormalizeData(heart.query)
    heart.anchors <- FindTransferAnchors(reference = heart.ref, query = heart.query, dims = 1:30,
        reference.reduction = "pca")
    
    # get both levels of anno
    predictions <- TransferData(anchorset = heart.anchors, refdata = heart.ref$celltypes.0.5, dims = 1:30)
    heart.query <- AddMetaData(heart.query, metadata = predictions)
    
    # add predictions to data.frame to save
    newdf = data.frame(barcode = rownames(heart.query@meta.data), class = heart.query$predicted.id,
                      class_prob = heart.query$prediction.score.max)
    # newdf[1:3,]

    # save
    write.table(newdf, file = paste0('annotations/', stages[sampleid], '_', samples[sampleid], '_Mantri_Seurat_label_transfer.csv'), 
                sep = ',', row.names = F, col.names = T, quote = F)
    
    setTxtProgressBar(pb, sampleid)
}

Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2355 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2348 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2224 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2694 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2776 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2810 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2313 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2240 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2308 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

